In [0]:
#Big Data Final Project Data Questions: 
    
#Ashley 
#Do roadways with traffic control devices have less crashes overall? 
#What are the top predictors that influence higher crash rates? 
#Are there any correlations between car damage amount and injuries? 

#Meet 
#Does weather condition impact crash type and fatalities? 
#Does weather/roadway condition have an impact on overall crashes? And out of those crashes how many are fatal? Provide top 5 arranging by the top number of fatalities. 
#What are the top causes of crashes overall and the total number of injuries associated with them? (include all relevant factors) 

#Patricia 
#Do traffic accidents tend to occur more frequently during specific months compared to others, and what are the weather conditions during these incidents?
#Accidents by month and weather condition
#Do crashes occur more frequently on weekdays or weekends? 
#What is the average number of vehicles involved in severe crashes?  
                                                                    
#Cody 
#What types of crashes result in the most injuries? (crash_type) 
#Are crashes more likely to occur at intersections or non-intersections 
#Which weather conditions contribute to the most severe injuries or fatalities and how much? 
#New Question 3: "How do different weather conditions contribute to the severity of crash injuries over time, and which conditions pose the highest risk of severe or fatal outcomes each month?"

In [0]:
# Python code for Machine learning: 
# Common imports
import numpy as np
import pandas as pd
from sklearn.compose import ColumnTransformer
from sklearn.pipeline import Pipeline
from sklearn.impute import SimpleImputer
from sklearn.preprocessing import StandardScaler
from sklearn.preprocessing import OneHotEncoder
from sklearn.preprocessing import FunctionTransformer
from sklearn.preprocessing import LabelEncoder
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.decomposition import TruncatedSVD
from sklearn.metrics import classification_report, confusion_matrix
from sklearn.model_selection import train_test_split, GridSearchCV, cross_val_score
from sklearn.ensemble import RandomForestClassifier
from sklearn.dummy import DummyClassifier
from sklearn.dummy import DummyRegressor
from sklearn.metrics import mean_squared_error
from sklearn.tree import DecisionTreeRegressor
import matplotlib.pyplot as plt
import seaborn as sns
from pyspark.sql import SparkSession
from pyspark.sql.functions import col, when, isnull, count, lower, sum, to_date, trim, avg, lit
from pyspark.ml.feature import StringIndexer, OneHotEncoder, VectorAssembler, StandardScaler
from pyspark.ml import Pipeline
from pyspark.ml.regression import DecisionTreeRegressor
from pyspark.ml.evaluation import RegressionEvaluator
from pyspark.ml.feature import Imputer
from pyspark.sql.types import NumericType, StringType
from pyspark.sql import functions as F

from functools import reduce
#from xgboost import XGBClassifier



In [0]:
# File location and type
file_location = "/FileStore/tables/final_project_big_data_2.csv"
file_type = "csv"

# CSV options
infer_schema = "true"
first_row_is_header = "true"
delimiter = ","

# The applied options are for CSV files. For other file types, these will be ignored.
df = spark.read.format(file_type) \
  .option("inferSchema", infer_schema) \
  .option("header", first_row_is_header) \
  .option("sep", delimiter) \
  .load(file_location)

#Display imported data
#display(df)

# Create a view or table

temp_table_name = "final_group_project_csv"

df.createOrReplaceTempView(temp_table_name)


In [0]:
from pyspark.sql.functions import when, trim, col, lower
from functools import reduce
from pyspark.sql import functions as F

df = spark.read.csv("/FileStore/shared_uploads/finalprojectgroup4040@gmail.com/export__1_.csv", header=True, inferSchema=True)
crashmaster = df

#Ordinal encoding
crashmaster = crashmaster.withColumn(
    "damage",
    trim(crashmaster["damage"])
).withColumn(
    "damage",
    when(col("damage") == "$500 OR LESS", 0)
    .when(col("damage") == "$501 - $1,500", 1)
    .when(col("damage") == "OVER $1,500", 2)
    .otherwise(None)
)


# List of string columns to check for 'unknown' or 'other'
string_cols = [col_name for col_name, dtype in crashmaster.dtypes if dtype == "string"]

# Build the filter condition for each unwanted value
unknown_filter = ~reduce(lambda x, y: x | y, [lower(col(c)).contains("unknown") for c in string_cols])
other_filter = ~reduce(lambda x, y: x | y, [lower(col(c)).contains("other") for c in string_cols])

# Apply filters
crashmaster = crashmaster.filter(unknown_filter & other_filter)

# Check for missing data
from pyspark.sql import functions as F

crashmaster.select([
    F.sum(F.col(c).isNull().cast("int")).alias(c) for c in crashmaster.columns
 ]).toPandas().T

# Store the 'crashmaster' DataFrame into a table named 'cleaned_data'
crashmaster.createOrReplaceTempView("cleaned_data") #create temp view



In [0]:
# Drop the table if it exists
spark.sql("DROP TABLE IF EXISTS cleaned_data")

# Now, create the table
spark.sql("CREATE TABLE cleaned_data AS SELECT * FROM cleaned_data")

---------------------------------------------------------------------------
AnalysisException                         Traceback (most recent call last)
File <command-2815889829997577>, line 5
      2 spark.sql("DROP TABLE IF EXISTS cleaned_data")
      4 # Now, create the table
----> 5 spark.sql("CREATE TABLE cleaned_data AS SELECT * FROM cleaned_data")

File /databricks/spark/python/pyspark/instrumentation_utils.py:47, in _wrap_function.<locals>.wrapper(*args, **kwargs)
     45 start = time.perf_counter()
     46 try:
---> 47     res = func(*args, **kwargs)
     48     logger.log_success(
     49         module_name, class_name, function_name, time.perf_counter() - start, signature
     50     )
     51     return res

File /databricks/spark/python/pyspark/sql/session.py:1830, in SparkSession.sql(self, sqlQuery, args, **kwargs)
   1825     else:
   1826         raise PySparkTypeError(
   1827             error_class="INVALID_TYPE",
   1828             message_parameters={"arg_name": "

In [0]:
display(crashmaster)
crashmaster.count()

crash_date traffic_control_device weather_condition lighting_condition first_crash_type trafficway_type alignment roadway_surface_cond road_defect crash_type intersection_related_i damage prim_contributory_cause num_units most_severe_injury injuries_total injuries_fatal injuries_incapacitating injuries_non_incapacitating injuries_reported_not_evident injuries_no_indication crash_hour crash_day_of_week crash_month 8132023 TRAFFIC SIGNAL CLEAR DARKNESS, LIGHTED ROAD TURNING FOUR WAY STRAIGHT AND LEVEL DRY NO DEFECTS NO INJURY / DRIVE AWAY Y 2 IMPROPER TURNING/NO SIGNAL 2 NO INDICATION OF INJURY 0 0 0 0 0 2 0 1 8 12092021 TRAFFIC SIGNAL CLEAR DAYLIGHT REAR END T-INTERSECTION STRAIGHT AND LEVEL DRY NO DEFECTS NO INJURY / DRIVE AWAY Y 1 FOLLOWING TOO CLOSELY 3 NO INDICATION OF INJURY 0 0 0 0 0 3 10 5 12 8092023 TRAFFIC SIGNAL CLEAR DAYLIGHT ANGLE FOUR WAY STRAIGHT AND LEVEL DRY NO DEFECTS INJURY AND / OR TOW DUE TO CRASH Y 2 UNABLE TO DETERMINE 2 NONINCAPACITATING INJURY 5 0 0 5 0 0 19 4 8 12202022 TRAFFIC SIGNAL CLEAR DAYLIGHT REAR TO FRONT FOUR WAY STRAIGHT AND LEVEL DRY NO DEFECTS NO INJURY / DRIVE AWAY Y 1 IMPROPER BACKING 2 NO INDICATION OF INJURY 0 0 0 0 0 2 11 3 12 9202023 NO CONTROLS CLEAR DAYLIGHT ANGLE DIVIDED - W/MEDIAN (NOT RAISED) CURVE, LEVEL DRY NO DEFECTS INJURY AND / OR TOW DUE TO CRASH Y 2 FAILING TO YIELD RIGHT-OF-WAY 2 NONINCAPACITATING INJURY 1 0 0 1 0 1 14 4 9 6042018 TRAFFIC SIGNAL CLEAR DAYLIGHT REAR END NOT DIVIDED STRAIGHT AND LEVEL DRY NO DEFECTS NO INJURY / DRIVE AWAY Y 2 FOLLOWING TOO CLOSELY 2 NO INDICATION OF INJURY 0 0 0 0 0 3 18 2 6 9072023 STOP SIGN/FLASHER CLEAR DAYLIGHT ANGLE FOUR WAY STRAIGHT AND LEVEL DRY NO DEFECTS NO INJURY / DRIVE AWAY Y 2 FAILING TO YIELD RIGHT-OF-WAY 2 NO INDICATION OF INJURY 0 0 0 0 0 4 17 5 9 8092023 NO CONTROLS CLEAR DAYLIGHT SIDESWIPE SAME DIRECTION ONE-WAY STRAIGHT AND LEVEL DRY NO DEFECTS NO INJURY / DRIVE AWAY Y 2 IMPROPER OVERTAKING/PASSING 2 NO INDICATION OF INJURY 0 0 0 0 0 2 7 4 8 2092020 TRAFFIC SIGNAL SNOW DAYLIGHT REAR END RAMP STRAIGHT AND LEVEL SNOW OR SLUSH NO DEFECTS NO INJURY / DRIVE AWAY Y 2 FOLLOWING TOO CLOSELY 2 NO INDICATION OF INJURY 0 0 0 0 0 2 14 1 2 8012023 NO CONTROLS CLEAR DARKNESS, LIGHTED ROAD SIDESWIPE OPPOSITE DIRECTION NOT DIVIDED STRAIGHT AND LEVEL DRY NO DEFECTS INJURY AND / OR TOW DUE TO CRASH N 2 IMPROPER TURNING/NO SIGNAL 4 INCAPACITATING INJURY 1 0 1 0 0 1 23 3 8 8012023 TRAFFIC SIGNAL CLEAR DAYLIGHT PEDALCYCLIST TRAFFIC ROUTE STRAIGHT AND LEVEL DRY NO DEFECTS INJURY AND / OR TOW DUE TO CRASH N 0 DRIVING ON WRONG SIDE/WRONG WAY 2 REPORTED, NOT EVIDENT 1 0 0 0 1 1 15 3 8 9052023 TRAFFIC SIGNAL CLEAR DUSK ANGLE FIVE POINT, OR MORE STRAIGHT AND LEVEL DRY NO DEFECTS INJURY AND / OR TOW DUE TO CRASH Y 2 UNABLE TO DETERMINE 2 INCAPACITATING INJURY 3 0 1 2 0 2 19 3 9 9092022 TRAFFIC SIGNAL CLEAR DAYLIGHT SIDESWIPE SAME DIRECTION FOUR WAY STRAIGHT AND LEVEL DRY NO DEFECTS NO INJURY / DRIVE AWAY Y 2 IMPROPER LANE USAGE 2 NO INDICATION OF INJURY 0 0 0 0 0 2 16 6 9 8222023 NO CONTROLS CLEAR DAYLIGHT REAR END NOT DIVIDED STRAIGHT AND LEVEL DRY NO DEFECTS NO INJURY / DRIVE AWAY Y 2 UNABLE TO DETERMINE 2 NO INDICATION OF INJURY 0 0 0 0 0 2 15 3 8 8022023 TRAFFIC SIGNAL CLEAR DARKNESS, LIGHTED ROAD TURNING FOUR WAY STRAIGHT AND LEVEL DRY NO DEFECTS NO INJURY / DRIVE AWAY Y 2 FAILING TO YIELD RIGHT-OF-WAY 2 NO INDICATION OF INJURY 0 0 0 0 0 3 20 4 8 9062023 STOP SIGN/FLASHER CLEAR DAYLIGHT TURNING T-INTERSECTION STRAIGHT AND LEVEL DRY NO DEFECTS INJURY AND / OR TOW DUE TO CRASH Y 2 UNABLE TO DETERMINE 2 REPORTED, NOT EVIDENT 1 0 0 0 1 1 14 4 9 9062023 STOP SIGN/FLASHER CLEAR DAYLIGHT REAR END T-INTERSECTION STRAIGHT AND LEVEL DRY NO DEFECTS NO INJURY / DRIVE AWAY Y 2 FAILING TO YIELD RIGHT-OF-WAY 2 NO INDICATION OF INJURY 0 0 0 0 0 2 14 4 9 8172023 STOP SIGN/FLASHER CLEAR DAYLIGHT TURNING FOUR WAY STRAIGHT AND LEVEL DRY NO DEFECTS NO INJURY / DRIVE AWAY Y 2 FAILING TO YIELD RIGHT-OF-WAY 2 NO INDICATION OF INJURY 0 0 0 0 0 2 13 5 8 3202022 NO CONTRO

162320

In [0]:
#Does weather/roadway condition have an impact on overall crashes? And out of those crashes how many are fatal? Provide top 5 arranging by the top number of fatalities.

# Execute the SQL query and store the result in a DataFrame
df = spark.sql("""
    SELECT
        DISTINCT roadway_surface_cond AS `Road Surface Condition`,
        weather_condition AS `Weather Condition`,
        COUNT(*) AS `Overall Crashes`,
        SUM(injuries_fatal) AS `Overall Fatalities`
    FROM cleaned_data
    GROUP BY `Weather Condition`, `Road Surface Condition`
    ORDER BY `Overall Fatalities` DESC
    LIMIT 5
""")

display(df)

Road Surface Condition Weather Condition Overall Crashes Overall Fatalities DRY CLEAR 126233 249 WET RAIN 16264 31 DRY CLOUDY/OVERCAST 4053 8 WET CLEAR 5521 6 SNOW OR SLUSH CLEAR 1017 3

Databricks visualization. Run in Databricks to view.

In [0]:
%sql

--Does weather condition impact crash type and fatalities? 

SELECT weather_condition AS Weather_Condition, crash_type AS Crash_Type,
COUNT(*) AS Overall_Crash,
SUM(injuries_fatal) AS Overall_Fatalities
FROM cleaned_data
GROUP BY Weather_Condition, Crash_Type
ORDER BY Overall_Fatalities DESC
LIMIT 5;

Weather_Condition Crash_Type Overall_Crash Overall_Fatalities CLEAR INJURY AND / OR TOW DUE TO CRASH 59710 259 RAIN INJURY AND / OR TOW DUE TO CRASH 8335 31 CLOUDY/OVERCAST INJURY AND / OR TOW DUE TO CRASH 2796 10 SNOW INJURY AND / OR TOW DUE TO CRASH 2221 3 SEVERE CROSS WIND GATE INJURY AND / OR TOW DUE TO CRASH 11 1

Databricks visualization. Run in Databricks to view.

In [0]:
%sql

--What are the top causes of crashes overall and the total number of injuries associated with them? (include all relevant factors)

SELECT traffic_control_device AS `Traffic Device`,
weather_condition AS `Weather Condition`,
lighting_condition AS `Lighting Condition`,
first_crash_type AS `First Crash Type`,
trafficway_type AS `Road Type`,
alignment AS `Allignment`,
roadway_surface_cond AS `Road Surface Condition`,
road_defect AS `Road Defects`,
crash_type AS `Crash Type`,
prim_contributory_cause AS `Primary Cause`,
COUNT(*) AS `Total Number Of Injuries`
FROM cleaned_data
GROUP BY `Traffic Device`, `Weather Condition`, `Lighting Condition`, `First Crash Type`, `Road Type`, `Allignment`, `Road Surface Condition`, `Road Defects`, `Crash Type`, `Primary Cause`
ORDER BY `Total Number Of Injuries` DESC
LIMIT 1

Traffic Device Weather Condition Lighting Condition First Crash Type Road Type Allignment Road Surface Condition Road Defects Crash Type Primary Cause Total Number Of Injuries TRAFFIC SIGNAL CLEAR DAYLIGHT REAR END NOT DIVIDED STRAIGHT AND LEVEL DRY NO DEFECTS NO INJURY / DRIVE AWAY FOLLOWING TOO CLOSELY 2173

In [0]:
%sql
--#Do roadways with traffic control devices have less crashes overall? 
SELECT traffic_control_device, 
COUNT(*) AS total_crashes
FROM cleaned_data
GROUP BY traffic_control_device
ORDER BY total_crashes DESC;


traffic_control_device total_crashes TRAFFIC SIGNAL 98198 STOP SIGN/FLASHER 39000 NO CONTROLS 24147 YIELD 368 PEDESTRIAN CROSSING SIGN 189 LANE USE MARKING 122 FLASHING CONTROL SIGNAL 106 POLICE/FLAGMAN 78 RAILROAD CROSSING GATE 58 SCHOOL ZONE 19 DELINEATORS 10 RR CROSSING SIGN 9 NO PASSING 8 BICYCLE CROSSING SIGN 8

Databricks visualization. Run in Databricks to view.

In [0]:
%sql

--#Comparing roadways with vs without traffic control devices
SELECT 
    CASE 
        WHEN traffic_control_device IS NULL OR traffic_control_device = 'None' THEN 'No Control'
        ELSE 'With Control'
    END AS control_status,
    COUNT(*) AS total_crashes
FROM cleaned_data
GROUP BY control_status;

-- Adding total percentage and filtering out nulls for cleaner results
SELECT 
  traffic_control_device,
  COUNT(*) AS total_crashes,
  ROUND(COUNT(*) * 100.0 / SUM(COUNT(*)) OVER (), 2) AS pct_of_total
FROM cleaned_data
WHERE traffic_control_device IS NOT NULL
GROUP BY traffic_control_device
ORDER BY total_crashes DESC;



traffic_control_device total_crashes pct_of_total TRAFFIC SIGNAL 98198 60.50 STOP SIGN/FLASHER 39000 24.03 NO CONTROLS 24147 14.88 YIELD 368 0.23 PEDESTRIAN CROSSING SIGN 189 0.12 LANE USE MARKING 122 0.08 FLASHING CONTROL SIGNAL 106 0.07 POLICE/FLAGMAN 78 0.05 RAILROAD CROSSING GATE 58 0.04 SCHOOL ZONE 19 0.01 DELINEATORS 10 0.01 RR CROSSING SIGN 9 0.01 NO PASSING 8 0.00 BICYCLE CROSSING SIGN 8 0.00

In [0]:
%sql
--#What are the top predictors that influence higher crash rates? 
SELECT 
  PRIM_CONTRIBUTORY_CAUSE, 
  COUNT(*) AS crash_count
FROM cleaned_data
GROUP BY PRIM_CONTRIBUTORY_CAUSE
ORDER BY crash_count DESC
LIMIT 10;


--Exploring other variables influencing crash rate
--Crashes by weaher condition
SELECT 
  WEATHER_CONDITION, 
  COUNT(*) AS crash_count
FROM cleaned_data
GROUP BY WEATHER_CONDITION
ORDER BY crash_count DESC;

--Crashes by roadway surface condition
SELECT 
  ROADWAY_SURFACE_COND, 
  COUNT(*) AS crash_count
FROM cleaned_data
GROUP BY ROADWAY_SURFACE_COND
ORDER BY crash_count DESC;

--#Crashes by lighting condition
SELECT 
  LIGHTING_CONDITION, 
  COUNT(*) AS crash_count
FROM cleaned_data
GROUP BY LIGHTING_CONDITION
ORDER BY crash_count DESC;

--Crashes by weather and roadway condition
SELECT 
  WEATHER_CONDITION, 
  ROADWAY_SURFACE_COND,
  COUNT(*) AS crash_count
FROM cleaned_data
GROUP BY WEATHER_CONDITION, ROADWAY_SURFACE_COND
ORDER BY crash_count DESC
LIMIT 10;


WEATHER_CONDITION ROADWAY_SURFACE_COND crash_count CLEAR DRY 126233 RAIN WET 16264 CLEAR WET 5521 CLOUDY/OVERCAST DRY 4053 SNOW SNOW OR SLUSH 3253 CLOUDY/OVERCAST WET 1790 SNOW WET 1604 CLEAR SNOW OR SLUSH 1017 CLEAR ICE 557 RAIN DRY 396

Databricks visualization. Run in Databricks to view.

In [0]:
%sql
--Are there any correlations between car damage amount and injuries?
SELECT 
  damage
  injuries_total,
  COUNT(*) AS total_crashes
FROM cleaned_data
GROUP BY damage, injuries_total
ORDER BY damage, total_crashes DESC;

--#Average injuries per damage amount
SELECT  
  damage,
  AVG(injuries_total) AS avg_injuries
FROM cleaned_data
GROUP BY damage
ORDER BY avg_injuries DESC;

-- Add percent of total crashes and avg injuries per damage level
SELECT 
  damage,
  COUNT(*) AS crash_count,
  ROUND(COUNT(*) * 100.0 / SUM(COUNT(*)) OVER (), 2) AS pct_of_total,
  ROUND(AVG(injuries_total), 2) AS avg_injuries
FROM cleaned_data
WHERE damage IS NOT NULL
GROUP BY damage
ORDER BY avg_injuries DESC;

SELECT 
  CASE 
    WHEN damage = 0 THEN 'Low'
    WHEN damage = 1 THEN 'Medium'
    WHEN damage = 2 THEN 'High'
    ELSE 'Unknown'
  END AS damage,
  ROUND(AVG(injuries_total), 2) AS avg_injuries
FROM cleaned_data
GROUP BY damage
ORDER BY avg_injuries DESC;




damage avg_injuries High 0.46 Low 0.39 Medium 0.16

Databricks visualization. Run in Databricks to view.

In [0]:
%sql
--Do traffic accidents tend to occur more frequently during specific months compared to others,
 --and what are the weather conditions during these incidents?

SELECT
    CASE t1.crash_month
        WHEN 1 THEN 'January'
        WHEN 2 THEN 'February'
        WHEN 3 THEN 'March'
        WHEN 4 THEN 'April'
        WHEN 5 THEN 'May'
        WHEN 6 THEN 'June'
        WHEN 7 THEN 'July'
        WHEN 8 THEN 'August'
        WHEN 9 THEN 'September'
        WHEN 10 THEN 'October'
        WHEN 11 THEN 'November'
        WHEN 12 THEN 'December'
    END AS month_name,
    t2.weather_condition,
    t2.weather_count
FROM (
    SELECT
        crash_month,
        COUNT(*) AS total_accidents
    FROM cleaned_data
    GROUP BY crash_month
) t1
JOIN (
    SELECT
        crash_month,
        weather_condition,
        COUNT(*) AS weather_count,
        ROW_NUMBER() OVER(PARTITION BY crash_month ORDER BY COUNT(*) DESC) as rn
    FROM cleaned_data
    GROUP BY crash_month, weather_condition
) t2 ON t1.crash_month = t2.crash_month AND t2.rn = 1
ORDER BY t1.crash_month;

month_name weather_condition weather_count January CLEAR 8873 February CLEAR 8524 March CLEAR 9590 April CLEAR 9229 May CLEAR 11407 June CLEAR 12361 July CLEAR 12702 August CLEAR 12986 September CLEAR 13186 October CLEAR 12254 November CLEAR 11170 December CLEAR 11058

Databricks visualization. Run in Databricks to view.

In [0]:
%sql
-- 3. Accidents by month and weather condition
SELECT 
    CASE crash_month
        WHEN 1 THEN 'January'
        WHEN 2 THEN 'February'
        WHEN 3 THEN 'March'
        WHEN 4 THEN 'April'
        WHEN 5 THEN 'May'
        WHEN 6 THEN 'June'
        WHEN 7 THEN 'July'
        WHEN 8 THEN 'August'
        WHEN 9 THEN 'September'
        WHEN 10 THEN 'October'
        WHEN 11 THEN 'November'
        WHEN 12 THEN 'December'
    END AS month_name,
    weather_condition,
    COUNT(*) AS total_accidents
FROM cleaned_data
GROUP BY crash_month, weather_condition
ORDER BY crash_month, total_accidents DESC;



month_name weather_condition total_accidents January CLEAR 8873 January SNOW 1789 January RAIN 928 January CLOUDY/OVERCAST 678 January FREEZING RAIN/DRIZZLE 143 January FOG/SMOKE/HAZE 80 January SLEET/HAIL 75 January BLOWING SNOW 24 January SEVERE CROSS WIND GATE 2 February CLEAR 8524 February SNOW 1375 February RAIN 718 February CLOUDY/OVERCAST 377 February SLEET/HAIL 46 February BLOWING SNOW 35 February FOG/SMOKE/HAZE 30 February FREEZING RAIN/DRIZZLE 25 February SEVERE CROSS WIND GATE 5 March CLEAR 9590 March RAIN 1420 March CLOUDY/OVERCAST 561 March SNOW 273 March SLEET/HAIL 25 March FREEZING RAIN/DRIZZLE 23 March FOG/SMOKE/HAZE 10 March BLOWING SNOW 4 March SEVERE CROSS WIND GATE 2 April CLEAR 9229 April RAIN 1730 April CLOUDY/OVERCAST 496 April SNOW 264 April FREEZING RAIN/DRIZZLE 35 April SLEET/HAIL 27 April FOG/SMOKE/HAZE 3 April SEVERE CROSS WIND GATE 1 April BLOWING SNOW 1 May CLEAR 11407 May RAIN 1666 May CLOUDY/OVERCAST 590 May FOG/SMOKE/HAZE 9 May FREEZING RAIN/DRIZZLE 8 May SNOW 1 June CLEAR 12361 June RAIN 1191 June CLOUDY/OVERCAST 380 June FOG/SMOKE/HAZE 28 June FREEZING RAIN/DRIZZLE 5 June SNOW 3 June SEVERE CROSS WIND GATE 1 July CLEAR 12702 July RAIN 906 July CLOUDY/OVERCAST 320 July FOG/SMOKE/HAZE 10 July FREEZING RAIN/DRIZZLE 5 July SNOW 3 August CLEAR 12986 August RAIN 911 August CLOUDY/OVERCAST 364 August FOG/SMOKE/HAZE 5 August FREEZING RAIN/DRIZZLE 4 August SNOW 2 August BLOWING SAND, SOIL, DIRT 1 August SEVERE CROSS WIND GATE 1 September CLEAR 13186 September RAIN 1312 September CLOUDY/OVERCAST 373 September FREEZING RAIN/DRIZZLE 11 September FOG/SMOKE/HAZE 5 September SLEET/HAIL 3 October CLEAR 12254 October RAIN 2625 October CLOUDY/OVERCAST 640 October SNOW 119 October FREEZING RAIN/DRIZZLE 23 October FOG/SMOKE/HAZE 20 October SLEET/HAIL 7 October SEVERE CROSS WIND GATE 2 October BLOWING SNOW 2 November CLEAR 11170 November RAIN 1682 November CLOUDY/OVERCAST 618 November SNOW 613 November FREEZING RAIN/DRIZZLE 57 November SLEET/HAIL 27 November FOG/SMOKE/HAZE 15 November BLOWING SNOW 6 November SEVERE CROSS WIND GATE 2 December CLEAR 11058 December RAIN 1657 December SNOW 757 December CLOUDY/OVERCAST 623 December FOG/SMOKE/HAZE 66 December FREEZING RAIN/DRIZZLE 45 December SLEET/HAIL 37 December BLOWING SNOW 10 December SEVERE CROSS WIND GATE 4

Databricks visualization. Run in Databricks to view.

In [0]:
%sql
SELECT
    CASE
        WHEN crash_day_of_week IN (1, 7) THEN 'Weekend'
        ELSE 'Weekday'
    END AS day_type,
    COUNT(*) AS crash_count
FROM
    cleaned_data
GROUP BY
    day_type
ORDER BY
    crash_count DESC;

day_type crash_count Weekday 119188 Weekend 43132

Databricks visualization. Run in Databricks to view.

In [0]:
%sql

SELECT
    AVG(num_units * 1.0) AS avg_vehicles_in_severe_crashes
FROM
    cleaned_data
WHERE
    most_severe_injury IN ('INCAPACITATING INJURY', 'FATAL INJURY');

avg_vehicles_in_severe_crashes 2.18754

In [0]:
%sql
-- What types of crashes result in the most injuries? (crash_type) 
SELECT crash_type AS `Crash Type`, 
COUNT(*) AS `Total Injuries` 
FROM cleaned_data 
GROUP BY crash_type 
ORDER BY "Total Injuries" DESC;

Crash Type Total Injuries INJURY AND / OR TOW DUE TO CRASH 73617 NO INJURY / DRIVE AWAY 88703

In [0]:
%sql
--Are crashes more likely to occur at intersections or non-intersections 
SELECT 

CASE 
WHEN trafficway_type LIKE '%INTERSECTION%' THEN 'INTERSECTION'
ELSE 'Others'
END AS `Intersection_Type`,

COUNT(*) AS `Total`
FROM cleaned_data

GROUP BY CASE 
WHEN trafficway_type LIKE '%INTERSECTION%' THEN 'INTERSECTION'
ELSE 'Others'
END;

Intersection_Type Total INTERSECTION 7826 Others 154494

Databricks visualization. Run in Databricks to view.

In [0]:
%sql
--Which weather condition contributes to the most severe injuries or fatalities and how much? 
SELECT 
    CASE 
        WHEN most_severe_injury LIKE 'INCAPACITATING INJURY' OR most_severe_injury LIKE 'FATAL' THEN 'Severe Injury/Fatal'
    END AS `Injury_Type`,
    weather_condition,
    COUNT(*) AS `Total`
FROM cleaned_data
WHERE most_severe_injury LIKE 'INCAPACITATING INJURY' 
   OR most_severe_injury LIKE 'FATAL'
GROUP BY 
    CASE 
        WHEN most_severe_injury LIKE 'INCAPACITATING INJURY' OR most_severe_injury LIKE 'FATAL' THEN 'Severe Injury/Fatal'
    END,
    weather_condition
ORDER BY `Total` DESC;

Injury_Type weather_condition Total Severe Injury/Fatal CLEAR 4654 Severe Injury/Fatal RAIN 560 Severe Injury/Fatal CLOUDY/OVERCAST 181 Severe Injury/Fatal SNOW 111 Severe Injury/Fatal FREEZING RAIN/DRIZZLE 15 Severe Injury/Fatal SLEET/HAIL 10 Severe Injury/Fatal FOG/SMOKE/HAZE 6 Severe Injury/Fatal BLOWING SNOW 4 Severe Injury/Fatal SEVERE CROSS WIND GATE 1

In [0]:
%sql
-- How do different weather conditions contribute to the severity of crash injuries over time, and which conditions pose the highest risk of severe or fatal outcomes each month?
WITH categorized_injuries AS (
  SELECT 
    weather_condition,
    crash_month,
    CASE 
      WHEN most_severe_injury IN ('FATAL', 'INCAPACITATING INJURY') THEN 'Severe Injury/Fatal'
      WHEN most_severe_injury IN ('NONINCAPACITATING INJURY', 'REPORTED, NOT EVIDENT') THEN 'Less Severe Injury'
      ELSE 'No/Unknown Injury'
    END AS injury_category
  FROM cleaned_data
  WHERE weather_condition IS NOT NULL
)

SELECT 
  weather_condition,
  crash_month,
  injury_category,
  COUNT(*) AS total_incidents,
  ROUND(100.0 * COUNT(*) / SUM(COUNT(*)) OVER (PARTITION BY crash_month), 2) AS percentage_of_month,
  RANK() OVER (PARTITION BY crash_month ORDER BY COUNT(*) DESC) AS rank_in_month
FROM categorized_injuries
GROUP BY weather_condition, crash_month, injury_category
ORDER BY crash_month, rank_in_month;


weather_condition crash_month injury_category total_incidents percentage_of_month rank_in_month CLEAR 1 No/Unknown Injury 6674 53.00 1 CLEAR 1 Less Severe Injury 1911 15.18 2 SNOW 1 No/Unknown Injury 1379 10.95 3 RAIN 1 No/Unknown Injury 657 5.22 4 CLOUDY/OVERCAST 1 No/Unknown Injury 519 4.12 5 SNOW 1 Less Severe Injury 371 2.95 6 CLEAR 1 Severe Injury/Fatal 288 2.29 7 RAIN 1 Less Severe Injury 236 1.87 8 CLOUDY/OVERCAST 1 Less Severe Injury 141 1.12 9 FREEZING RAIN/DRIZZLE 1 No/Unknown Injury 101 0.80 10 FOG/SMOKE/HAZE 1 No/Unknown Injury 52 0.41 11 SLEET/HAIL 1 No/Unknown Injury 45 0.36 12 FREEZING RAIN/DRIZZLE 1 Less Severe Injury 39 0.31 13 SNOW 1 Severe Injury/Fatal 39 0.31 13 RAIN 1 Severe Injury/Fatal 35 0.28 15 SLEET/HAIL 1 Less Severe Injury 28 0.22 16 FOG/SMOKE/HAZE 1 Less Severe Injury 26 0.21 17 BLOWING SNOW 1 No/Unknown Injury 19 0.15 18 CLOUDY/OVERCAST 1 Severe Injury/Fatal 18 0.14 19 BLOWING SNOW 1 Less Severe Injury 3 0.02 20 FREEZING RAIN/DRIZZLE 1 Severe Injury/Fatal 3 0.02 20 BLOWING SNOW 1 Severe Injury/Fatal 2 0.02 22 FOG/SMOKE/HAZE 1 Severe Injury/Fatal 2 0.02 22 SEVERE CROSS WIND GATE 1 No/Unknown Injury 2 0.02 22 SLEET/HAIL 1 Severe Injury/Fatal 2 0.02 22 CLEAR 2 No/Unknown Injury 6547 58.80 1 CLEAR 2 Less Severe Injury 1720 15.45 2 SNOW 2 No/Unknown Injury 1090 9.79 3 RAIN 2 No/Unknown Injury 528 4.74 4 CLOUDY/OVERCAST 2 No/Unknown Injury 288 2.59 5 CLEAR 2 Severe Injury/Fatal 257 2.31 6 SNOW 2 Less Severe Injury 252 2.26 7 RAIN 2 Less Severe Injury 167 1.50 8 CLOUDY/OVERCAST 2 Less Severe Injury 81 0.73 9 SLEET/HAIL 2 No/Unknown Injury 35 0.31 10 SNOW 2 Severe Injury/Fatal 33 0.30 11 BLOWING SNOW 2 No/Unknown Injury 27 0.24 12 FOG/SMOKE/HAZE 2 No/Unknown Injury 27 0.24 12 RAIN 2 Severe Injury/Fatal 23 0.21 14 FREEZING RAIN/DRIZZLE 2 No/Unknown Injury 19 0.17 15 SLEET/HAIL 2 Less Severe Injury 9 0.08 16 CLOUDY/OVERCAST 2 Severe Injury/Fatal 8 0.07 17 BLOWING SNOW 2 Less Severe Injury 7 0.06 18 SEVERE CROSS WIND GATE 2 No/Unknown Injury 4 0.04 19 FREEZING RAIN/DRIZZLE 2 Less Severe Injury 4 0.04 19 FOG/SMOKE/HAZE 2 Less Severe Injury 3 0.03 21 FREEZING RAIN/DRIZZLE 2 Severe Injury/Fatal 2 0.02 22 SLEET/HAIL 2 Severe Injury/Fatal 2 0.02 22 SEVERE CROSS WIND GATE 2 Less Severe Injury 1 0.01 24 BLOWING SNOW 2 Severe Injury/Fatal 1 0.01 24 CLEAR 3 No/Unknown Injury 7218 60.61 1 CLEAR 3 Less Severe Injury 2054 17.25 2 RAIN 3 No/Unknown Injury 1036 8.70 3 CLOUDY/OVERCAST 3 No/Unknown Injury 415 3.49 4 RAIN 3 Less Severe Injury 334 2.80 5 CLEAR 3 Severe Injury/Fatal 318 2.67 6 SNOW 3 No/Unknown Injury 210 1.76 7 CLOUDY/OVERCAST 3 Less Severe Injury 131 1.10 8 SNOW 3 Less Severe Injury 58 0.49 9 RAIN 3 Severe Injury/Fatal 50 0.42 10 SLEET/HAIL 3 No/Unknown Injury 18 0.15 11 CLOUDY/OVERCAST 3 Severe Injury/Fatal 15 0.13 12 FREEZING RAIN/DRIZZLE 3 No/Unknown Injury 14 0.12 13 FREEZING RAIN/DRIZZLE 3 Less Severe Injury 9 0.08 14 FOG/SMOKE/HAZE 3 No/Unknown Injury 7 0.06 15 SLEET/HAIL 3 Less Severe Injury 6 0.05 16 SNOW 3 Severe Injury/Fatal 5 0.04 17 BLOWING SNOW 3 No/Unknown Injury 4 0.03 18 SEVERE CROSS WIND GATE 3 No/Unknown Injury 2 0.02 19 FOG/SMOKE/HAZE 3 Less Severe Injury 2 0.02 19 FOG/SMOKE/HAZE 3 Severe Injury/Fatal 1 0.01 21 SLEET/HAIL 3 Severe Injury/Fatal 1 0.01 21 CLEAR 4 No/Unknown Injury 6866 58.26 1 CLEAR 4 Less Severe Injury 2067 17.54 2 RAIN 4 No/Unknown Injury 1234 10.47 3 RAIN 4 Less Severe Injury 436 3.70 4 CLOUDY/OVERCAST 4 No/Unknown Injury 357 3.03 5 CLEAR 4 Severe Injury/Fatal 296 2.51 6 SNOW 4 No/Unknown Injury 200 1.70 7 CLOUDY/OVERCAST 4 Less Severe Injury 121 1.03 8 SNOW 4 Less Severe Injury 60 0.51 9 RAIN 4 Severe Injury/Fatal 60 0.51 9 FREEZING RAIN/DRIZZLE 4 No/Unknown Injury 25 0.21 11 SLEET/HAIL 4 No/Unknown Injury 21 0.18 12 CLOUDY/OVERCAST 4 Severe Injury/Fatal 18 0.15 13 FREEZING RAIN/DRIZZLE 4 Less Severe Injury 7 0.06 14 SNOW 4 Severe Injury/Fatal 4 0.03 15 SLEET/HAIL 4 Less Severe Injury 4 0.03 15 FOG/SMOKE/HAZE 4 Less Severe Injury 3 0.03 17 FREEZING RAIN/DRIZZLE 4 Severe 

### **Machine Learning:**

In [0]:
# What types of crashes result in the most injuries?
#Pull cleaned data 
crash = crashmaster

# Now you can split it
train_set, test_set = crash.randomSplit([0.7, 0.3], seed=42)

# Target and input split, Trying to find the predictors for injuries.
# Target
label_col = "injuries_total"

# Separate features
train_inputs = train_set.drop(label_col)
test_inputs = test_set.drop(label_col)

com.databricks.backend.common.rpc.CommandSkippedException
	at com.databricks.spark.chauffeur.SequenceExecutionState.$anonfun$cancel$3(SequenceExecutionState.scala:138)
	at com.databricks.spark.chauffeur.SequenceExecutionState.$anonfun$cancel$3$adapted(SequenceExecutionState.scala:133)
	at scala.collection.immutable.Range.foreach(Range.scala:158)
	at com.databricks.spark.chauffeur.SequenceExecutionState.cancel(SequenceExecutionState.scala:133)
	at com.databricks.spark.chauffeur.ExecContextState.cancelRunningSequence(ExecContextState.scala:728)
	at com.databricks.spark.chauffeur.ExecContextState.$anonfun$cancel$1(ExecContextState.scala:446)
	at scala.Option.getOrElse(Option.scala:189)
	at com.databricks.spark.chauffeur.ExecContextState.cancel(ExecContextState.scala:446)
	at com.databricks.spark.chauffeur.ExecutionContextManagerV1.cancelExecution(ExecutionContextManagerV1.scala:464)
	at com.databricks.spark.chauffeur.ChauffeurState.$anonfun$process$1(ChauffeurState.scala:571)
	at com.data

In [0]:
# Find numeric columns
numeric_columns = [field.name for field in train_inputs.schema.fields if isinstance(field.dataType, NumericType)]

# Find categorical (string) columns
categorical_columns = [field.name for field in train_inputs.schema.fields if isinstance(field.dataType, StringType)]

# Print
print("Numeric columns are:", numeric_columns)
print("Categorical columns are:", categorical_columns)

com.databricks.backend.common.rpc.CommandSkippedException
	at com.databricks.spark.chauffeur.SequenceExecutionState.$anonfun$cancel$3(SequenceExecutionState.scala:138)
	at com.databricks.spark.chauffeur.SequenceExecutionState.$anonfun$cancel$3$adapted(SequenceExecutionState.scala:133)
	at scala.collection.immutable.Range.foreach(Range.scala:158)
	at com.databricks.spark.chauffeur.SequenceExecutionState.cancel(SequenceExecutionState.scala:133)
	at com.databricks.spark.chauffeur.ExecContextState.cancelRunningSequence(ExecContextState.scala:728)
	at com.databricks.spark.chauffeur.ExecContextState.$anonfun$cancel$1(ExecContextState.scala:446)
	at scala.Option.getOrElse(Option.scala:189)
	at com.databricks.spark.chauffeur.ExecContextState.cancel(ExecContextState.scala:446)
	at com.databricks.spark.chauffeur.ExecutionContextManagerV1.cancelExecution(ExecutionContextManagerV1.scala:464)
	at com.databricks.spark.chauffeur.ChauffeurState.$anonfun$process$1(ChauffeurState.scala:571)
	at com.data

In [0]:
# Numeric Transformer (Imputer for any missing values, and scalar)
imputer = Imputer(inputCols=numeric_columns, outputCols=[f"{col}_imputed" for col in numeric_columns])
assembler_numeric = VectorAssembler(inputCols=[f"{col}_imputed" for col in numeric_columns], outputCol="numeric_features")
scaler = StandardScaler(inputCol="numeric_features", outputCol="scaled_numeric_features")


# Create categorical pipeline
indexers = [StringIndexer(inputCol=col, outputCol=f"{col}_indexed", handleInvalid="keep") for col in categorical_columns]
encoders = [OneHotEncoder(inputCol=f"{col}_indexed", outputCol=f"{col}_encoded") for col in categorical_columns]

# Final features
feature_cols = ["scaled_numeric_features"] + [f"{col}_encoded" for col in categorical_columns]
assembler_final = VectorAssembler(inputCols=feature_cols, outputCol="features")

# Build pipeline
stages = [imputer, assembler_numeric, scaler] + indexers + encoders + [assembler_final]
pipeline = Pipeline(stages=stages)

com.databricks.backend.common.rpc.CommandSkippedException
	at com.databricks.spark.chauffeur.SequenceExecutionState.$anonfun$cancel$3(SequenceExecutionState.scala:138)
	at com.databricks.spark.chauffeur.SequenceExecutionState.$anonfun$cancel$3$adapted(SequenceExecutionState.scala:133)
	at scala.collection.immutable.Range.foreach(Range.scala:158)
	at com.databricks.spark.chauffeur.SequenceExecutionState.cancel(SequenceExecutionState.scala:133)
	at com.databricks.spark.chauffeur.ExecContextState.cancelRunningSequence(ExecContextState.scala:728)
	at com.databricks.spark.chauffeur.ExecContextState.$anonfun$cancel$1(ExecContextState.scala:446)
	at scala.Option.getOrElse(Option.scala:189)
	at com.databricks.spark.chauffeur.ExecContextState.cancel(ExecContextState.scala:446)
	at com.databricks.spark.chauffeur.ExecutionContextManagerV1.cancelExecution(ExecutionContextManagerV1.scala:464)
	at com.databricks.spark.chauffeur.ChauffeurState.$anonfun$process$1(ChauffeurState.scala:571)
	at com.data

### Transform: fit_transform() for TRAIN and transform() for TEST

In [0]:
# Fit and transform the train data
model = pipeline.fit(train_set)
train_pred = model.transform(train_set)

# Apply the pipeline to the test set
test_pred = model.transform(test_set)

# Show the transformed results
#train_transformed.show()
#test_transformed.show()

com.databricks.backend.common.rpc.CommandSkippedException
	at com.databricks.spark.chauffeur.SequenceExecutionState.$anonfun$cancel$3(SequenceExecutionState.scala:138)
	at com.databricks.spark.chauffeur.SequenceExecutionState.$anonfun$cancel$3$adapted(SequenceExecutionState.scala:133)
	at scala.collection.immutable.Range.foreach(Range.scala:158)
	at com.databricks.spark.chauffeur.SequenceExecutionState.cancel(SequenceExecutionState.scala:133)
	at com.databricks.spark.chauffeur.ExecContextState.cancelRunningSequence(ExecContextState.scala:728)
	at com.databricks.spark.chauffeur.ExecContextState.$anonfun$cancel$1(ExecContextState.scala:446)
	at scala.Option.getOrElse(Option.scala:189)
	at com.databricks.spark.chauffeur.ExecContextState.cancel(ExecContextState.scala:446)
	at com.databricks.spark.chauffeur.ExecutionContextManagerV1.cancelExecution(ExecutionContextManagerV1.scala:464)
	at com.databricks.spark.chauffeur.ChauffeurState.$anonfun$process$1(ChauffeurState.scala:571)
	at com.data

### Find the Baseline:

In [0]:
# Dummy Model (Predict Mean)
# Compute mean
label_mean = train_set.select(avg(label_col)).first()[0]

# Predict constant mean
train_dummy = train_pred.withColumn("prediction", lit(label_mean))
test_dummy = test_pred.withColumn("prediction", lit(label_mean))

# Evaluate
evaluator = RegressionEvaluator(labelCol=label_col, predictionCol="prediction", metricName="rmse")

train_rmse = evaluator.evaluate(train_dummy)
test_rmse = evaluator.evaluate(test_dummy)

print(f"Train RMSE (Dummy Model): {train_rmse}")
print(f"Test RMSE (Dummy Model): {test_rmse}")

com.databricks.backend.common.rpc.CommandSkippedException
	at com.databricks.spark.chauffeur.SequenceExecutionState.$anonfun$cancel$3(SequenceExecutionState.scala:138)
	at com.databricks.spark.chauffeur.SequenceExecutionState.$anonfun$cancel$3$adapted(SequenceExecutionState.scala:133)
	at scala.collection.immutable.Range.foreach(Range.scala:158)
	at com.databricks.spark.chauffeur.SequenceExecutionState.cancel(SequenceExecutionState.scala:133)
	at com.databricks.spark.chauffeur.ExecContextState.cancelRunningSequence(ExecContextState.scala:728)
	at com.databricks.spark.chauffeur.ExecContextState.$anonfun$cancel$1(ExecContextState.scala:446)
	at scala.Option.getOrElse(Option.scala:189)
	at com.databricks.spark.chauffeur.ExecContextState.cancel(ExecContextState.scala:446)
	at com.databricks.spark.chauffeur.ExecutionContextManagerV1.cancelExecution(ExecutionContextManagerV1.scala:464)
	at com.databricks.spark.chauffeur.ChauffeurState.$anonfun$process$1(ChauffeurState.scala:571)
	at com.data

### Decision Tree Model: 

In [0]:
# Decision Tree Model
# Now fit decision tree on transformed train data
tree = DecisionTreeRegressor(featuresCol="features", labelCol=label_col, maxDepth=3)
tree_model = tree.fit(train_pred)

# Predict
train_tree_pred = tree_model.transform(train_pred)
test_tree_pred = tree_model.transform(test_pred)

# Evaluate
train_rmse_tree = evaluator.evaluate(train_tree_pred)
test_rmse_tree = evaluator.evaluate(test_tree_pred)

print(f"Train RMSE (Decision Tree): {train_rmse_tree}")
print(f"Test RMSE (Decision Tree): {test_rmse_tree}")

com.databricks.backend.common.rpc.CommandSkippedException
	at com.databricks.spark.chauffeur.SequenceExecutionState.$anonfun$cancel$3(SequenceExecutionState.scala:138)
	at com.databricks.spark.chauffeur.SequenceExecutionState.$anonfun$cancel$3$adapted(SequenceExecutionState.scala:133)
	at scala.collection.immutable.Range.foreach(Range.scala:158)
	at com.databricks.spark.chauffeur.SequenceExecutionState.cancel(SequenceExecutionState.scala:133)
	at com.databricks.spark.chauffeur.ExecContextState.cancelRunningSequence(ExecContextState.scala:728)
	at com.databricks.spark.chauffeur.ExecContextState.$anonfun$cancel$1(ExecContextState.scala:446)
	at scala.Option.getOrElse(Option.scala:189)
	at com.databricks.spark.chauffeur.ExecContextState.cancel(ExecContextState.scala:446)
	at com.databricks.spark.chauffeur.ExecutionContextManagerV1.cancelExecution(ExecutionContextManagerV1.scala:464)
	at com.databricks.spark.chauffeur.ChauffeurState.$anonfun$process$1(ChauffeurState.scala:571)
	at com.data

## Machine Learning:
#  

In [0]:
#Pull cleaned data
crash = crashmaster

#display(dbutils.fs.ls("dbfs:/FileStore/"))
 
# Load the dataset
#crash = pd.read_csv("final_project_csv")
 
# Remove time from crash_date column
#crash['crash_date'] = pd.to_datetime(crash['crash_date']).dt.date
 
# Binary encoding: create target variable — injury vs. no injury
crash['injuries_total'] = pd.to_numeric(crash['injuries_total'], errors='coerce')
crash['injury_flag'] = crash['injuries_total'].apply(lambda x: 1 if x > 0 else 0)


#Feature Engineering
 
# Nighttime crash indicator (between 8 PM and 6 AM)
crash['night_crash'] = crash['crash_hour'].apply(lambda x: 1 if (x >= 20 or x <= 6) else 0)
 
# Weekend crash (Saturday=6, Sunday=7)
crash['weekend_crash'] = crash['crash_day_of_week'].apply(lambda x: 1 if x in [6, 7] else 0)
 
# Rush hour crash (7-9 AM or 4-6 PM)
crash['rush_hour_crash'] = crash['crash_hour'].apply(lambda x: 1 if (7 <= x <= 9 or 16 <= x <= 18) else 0)
 
# More than one vehicle involved
crash['multi_vehicle'] = crash['num_units'].apply(lambda x: 1 if x > 1 else 0)
 
# Any incapacitating injury
crash['any_incapacitating'] = crash['injuries_incapacitating'].apply(lambda x: 1 if x > 0 else 0)
 
# Any fatalities
crash['any_fatalities'] = crash['injuries_fatal'].apply(lambda x: 1 if x > 0 else 0)
 
# Drop columns that leak target or are now redundant
drop_cols = [
    'injuries_total', 'crash_date', 'injuries_incapacitating',
    'injuries_fatal', 'crash_hour', 'crash_day_of_week', 'crash_month'
]
crash = crash.drop(columns=drop_cols)
 
#Train/Test Split
 
train_set, test_set = train_test_split(crash, test_size=0.3, random_state=42)
 
# Separate target variable
train_y = train_set[['injury_flag']]
test_y = test_set[['injury_flag']]
train_inputs = train_set.drop(['injury_flag'], axis=1)
test_inputs = test_set.drop(['injury_flag'], axis=1)
 
#Preprocessing Pipeline
 
#Identify numeric and categorical columns
numeric_columns = train_inputs.select_dtypes(include=[np.number]).columns.tolist()
categorical_columns = train_inputs.select_dtypes(include=['object']).columns.tolist()
 
#Numeric Transformer
numeric_transformer = Pipeline(steps=[
    ('imputer', SimpleImputer(strategy='mean')),
    ('scaler', StandardScaler())
])
 
#Categorical Transformer
categorical_transformer = Pipeline(steps=[
    ('imputer', SimpleImputer(strategy='constant', fill_value='missing')),
    ('onehot', OneHotEncoder(handle_unknown='ignore'))
])
 
#Preprocessor
preprocessor = ColumnTransformer([
    ('num', numeric_transformer, numeric_columns),
    ('cat', categorical_transformer, categorical_columns)
], remainder='drop')
 
#Fit and transform the training data
train_x = preprocessor.fit_transform(train_inputs)
 
#Transform the test data
test_x = preprocessor.transform(test_inputs)
 
#Logistic regressio models
 
log_reg = LogisticRegression(max_iter=1000)
log_reg.fit(train_x, train_y.values.ravel())
 
# Predictions
train_pred = log_reg.predict(train_x)
test_pred = log_reg.predict(test_x)
 
#Model Evaluation
 
print("Train Classification Report:")
print(classification_report(train_y, train_pred))
 
print("Test Classification Report:")
print(classification_report(test_y, test_pred))
 
print("Test Confusion Matrix:")
print(confusion_matrix(test_y, test_pred))

---------------------------------------------------------------------------
PySparkValueError                         Traceback (most recent call last)
File <command-4487304168304733>, line 13
      2 crash = crashmaster
      4 #display(dbutils.fs.ls("dbfs:/FileStore/"))
      5  
      6 # Load the dataset
   (...)
     11  
     12 # Binary encoding: create target variable — injury vs. no injury
---> 13 crash['injuries_total'] = pd.to_numeric(crash['injuries_total'], errors='coerce')
     14 crash['injury_flag'] = crash['injuries_total'].apply(lambda x: 1 if x > 0 else 0)
     17 #Feature Engineering
     18  
     19 # Nighttime crash indicator (between 8 PM and 6 AM)

File /databricks/python/lib/python3.11/site-packages/pandas/core/tools/numeric.py:146, in to_numeric(arg, errors, downcast)
    143 is_index = False
    144 is_scalars = False
--> 146 if isinstance(arg, ABCSeries):
    147     is_series = True
    148     values = arg.values

File /databricks/python/lib/python3.11/si

In [0]:

# Start Spark session if needed
spark = SparkSession.builder.getOrCreate()

# Assume crashmaster is your cleaned Spark DataFrame
crash = crashmaster

from pyspark.sql import SparkSession
from pyspark.sql.functions import col, when 

# Binary encoding: injury vs no injury
crash = crash.withColumn("injury_flag", when(col("injuries_total") > 0, 1).otherwise(0))

# Feature Engineering
crash = crash.withColumn("night_crash", when((col("crash_hour") >= 20) | (col("crash_hour") <= 6), 1).otherwise(0)) \
.withColumn("weekend_crash", when(col("crash_day_of_week").isin(6, 7), 1).otherwise(0)) \
.withColumn("rush_hour_crash", when(((col("crash_hour") >= 7) & (col("crash_hour") <= 9)) |
((col("crash_hour") >= 16) & (col("crash_hour") <= 18)), 1).otherwise(0)) \
.withColumn("multi_vehicle", when(col("num_units") > 1, 1).otherwise(0)) \
.withColumn("any_incapacitating", when(col("injuries_incapacitating") > 0, 1).otherwise(0)) \
.withColumn("any_fatalities", when(col("injuries_fatal") > 0, 1).otherwise(0))

# Drop unnecessary columns
columns_to_drop = [
'injuries_total', 'crash_date', 'injuries_incapacitating',
'injuries_fatal', 'crash_hour', 'crash_day_of_week', 'crash_month'
]
crash = crash.drop(*columns_to_drop)

# Train/Test split
train_set, test_set = crash.randomSplit([0.7, 0.3], seed=42)

# Identify feature columns
target = "injury_flag"
feature_columns = [col for col in crash.columns if col != target]

# Automatically determine categorical and numeric columns
categorical_columns = [f.name for f in crash.schema.fields if str(f.dataType) == "StringType" and f.name in feature_columns]
numeric_columns = [f.name for f in crash.schema.fields if f.name in feature_columns and f.name not in categorical_columns]

# Index and encode categorical features
indexers = [StringIndexer(inputCol=col, outputCol=col + "_index", handleInvalid="keep") for col in categorical_columns]
encoders = [OneHotEncoder(inputCol=col + "_index", outputCol=col + "_encoded") for col in categorical_columns]

# Assemble feature vector
assembler_inputs = [col + "_encoded" for col in categorical_columns] + numeric_columns
assembler = VectorAssembler(inputCols=assembler_inputs, outputCol="features_raw")

# 1. Confirm the list of numeric feature columns (no nulls!)
numeric_columns = ['night_crash', 'weekend_crash', 'rush_hour_crash', 
'multi_vehicle', 'any_incapacitating', 'any_fatalities']

# 2. Fill any nulls with zero — this is mandatory before VectorAssembler
crash = crash.fillna(0, subset=numeric_columns)

# 3. Assemble features into a single vector column
assembler = VectorAssembler(inputCols=numeric_columns, outputCol="features_raw")

from pyspark.ml.feature import StandardScaler

# 4. Apply scaler (this should work as long as features_raw is a Vector)
scaler = StandardScaler(inputCol="features_raw", outputCol="features", withMean=True, withStd=True)

from pyspark.ml.classification import LogisticRegression

# Model
lr = LogisticRegression(labelCol=target, featuresCol="features", maxIter=1000)

# Pipeline
pipeline = Pipeline(stages=indexers + encoders + [assembler, scaler, lr])

# Fit model
model = pipeline.fit(train_set)

# Predictions
train_pred = model.transform(train_set)
test_pred = model.transform(test_set)

# Evaluation

from pyspark.ml.evaluation import MulticlassClassificationEvaluator

evaluator = MulticlassClassificationEvaluator(
labelCol=target,
predictionCol="prediction",
metricName="f1"  
)

evaluator = MulticlassClassificationEvaluator(labelCol=target, predictionCol="prediction", metricName="accuracy")

train_accuracy = evaluator.evaluate(train_pred)
test_accuracy = evaluator.evaluate(test_pred)

print(f"Train Accuracy: {train_accuracy:.4f}")
print(f"Test Accuracy: {test_accuracy:.4f}")


Train Accuracy: 0.7673
Test Accuracy: 0.7670


In [0]:
from pyspark.sql import SparkSession
import pyspark.sql.functions as F
from pyspark.ml import Pipeline
from pyspark.ml.feature import StringIndexer, VectorAssembler
from pyspark.ml.classification import RandomForestClassifier
from pyspark.ml.evaluation import MulticlassClassificationEvaluator
from pyspark.ml.tuning import ParamGridBuilder, CrossValidator

crash = crashmaster

# Feature Engineering: Extract crash_day_of_week and crash_hour
if "crash_time" in crash.columns:
    crash = crash.withColumn("crash_time", F.to_timestamp("crash_time"))
    crash = crash.withColumn("crash_day_of_week", F.dayofweek("crash_time"))  # 1 = Sunday
    crash = crash.withColumn("crash_hour", F.hour("crash_time"))

# Data Preprocessing: Drop rows with nulls in key columns
crash = crash.dropna(subset=["crash_month", "weather_condition", "lighting_condition", "roadway_surface_cond"])

# StringIndexing (encode) categorical features
weather_indexer = StringIndexer(inputCol="weather_condition", outputCol="weather_condition_index", handleInvalid="keep")
lighting_indexer = StringIndexer(inputCol="lighting_condition", outputCol="lighting_condition_index", handleInvalid="keep")
roadway_indexer = StringIndexer(inputCol="roadway_surface_cond", outputCol="roadway_surface_cond_index", handleInvalid="keep")

# Assemble all features into a single vector
assembler = VectorAssembler(
    inputCols=[
        "weather_condition_index",
        "lighting_condition_index",
        "roadway_surface_cond_index",
        "crash_day_of_week",
        "crash_hour"
    ],
    outputCol="features"
)

# Random Forest Model
rf = RandomForestClassifier(
    labelCol="crash_month",  # Corrected labelCol name
    featuresCol="features",
    numTrees=150,
    maxDepth=5,
    seed=42
)

# Create Pipeline
pipeline = Pipeline(stages=[weather_indexer, lighting_indexer, roadway_indexer, assembler, rf])

# Train-test split
train_data, test_data = crash.randomSplit([0.8, 0.2], seed=42)

# Fit model
model = pipeline.fit(train_data)

# Predict
predictions = model.transform(test_data)

# Evaluation Metrics
evaluator_acc = MulticlassClassificationEvaluator(labelCol="crash_month", predictionCol="prediction", metricName="accuracy")
accuracy = evaluator_acc.evaluate(predictions)

evaluator_f1 = MulticlassClassificationEvaluator(labelCol="crash_month", predictionCol="prediction", metricName="f1")
f1_score = evaluator_f1.evaluate(predictions)

print(f"Random Forest Test Accuracy = {accuracy:.4f}")
print(f"Random Forest Test F1 Score = {f1_score:.4f}")

# Confusion Matrix - using Spark
confusion_df = predictions.groupBy("crash_month", "prediction").count()

# Convert to Pandas for Seaborn
confusion_pd = confusion_df.toPandas()

# Create pivot table
pivot = confusion_pd.pivot(index='crash_month', columns='prediction', values='count').fillna(0)


import matplotlib.pyplot as plt
import seaborn as sns

# Confusion Matrix
plt.figure(figsize=(12, 8))
sns.heatmap(pivot, annot=True, fmt=".0f", cmap="Blues")
plt.title("Random Forest Confusion Matrix")
plt.xlabel("Predicted Month")
plt.ylabel("Actual Month")
plt.show()


# Optional: Cross-Validation for Random Forest
paramGrid = ParamGridBuilder() \
    .addGrid(rf.numTrees, [100, 150]) \
    .addGrid(rf.maxDepth, [3, 5]) \
    .build()

crossval = CrossValidator(
    estimator=pipeline,
    estimatorParamMaps=paramGrid,
    evaluator=MulticlassClassificationEvaluator(labelCol="crash_month", predictionCol="prediction", metricName="f1"),
    numFolds=5,
    parallelism=2
)

cv_model = crossval.fit(train_data)

print("Best Random Forest Model after Cross Validation:")
best_rf_model = cv_model.bestModel.stages[-1]
print(f"  - Best Num Trees: {best_rf_model.getNumTrees}")
print(f"  - Best Max Depth: {best_rf_model.getOrDefault('maxDepth')}")

# Final Evaluation on test set with Cross-Validated model
cv_predictions = cv_model.transform(test_data)

accuracy_cv = evaluator_acc.evaluate(cv_predictions)
f1_score_cv = evaluator_f1.evaluate(cv_predictions)

print(f"Cross-Validated Test Accuracy = {accuracy_cv:.4f}")
print(f"Cross-Validated Test F1 Score = {f1_score_cv:.4f}")

Random Forest Test Accuracy = 0.1424
Random Forest Test F1 Score = 0.1069


In [0]:

# Import necessary libraries
from pyspark.sql import SparkSession
import pyspark.sql.functions as F
from pyspark.ml import Pipeline
from pyspark.ml.feature import StringIndexer, VectorAssembler
from pyspark.ml.classification import RandomForestClassifier
from pyspark.ml.evaluation import MulticlassClassificationEvaluator
from pyspark.ml.tuning import ParamGridBuilder, CrossValidator

import matplotlib.pyplot as plt
import seaborn as sns
import pandas as pd


# Load the dataset
crash = crashmaster  

# Feature Engineering: Extract crash_day_of_week and crash_hour


if "crash_time" in crash.columns:
    crash = crash.withColumn("crash_time", F.to_timestamp("crash_time"))
    crash = crash.withColumn("crash_day_of_week", F.dayofweek("crash_time"))  # 1 = Sunday
    crash = crash.withColumn("crash_hour", F.hour("crash_time"))

# Data Preprocessing: Drop rows with nulls in key columns
crash = crash.dropna(subset=["crash_month", "weather_condition", "lighting_condition", "roadway_surface_cond"])

# StringIndexing (encode) categorical features
weather_indexer = StringIndexer(inputCol="weather_condition", outputCol="weather_condition_index")
lighting_indexer = StringIndexer(inputCol="lighting_condition", outputCol="lighting_condition_index")
roadway_indexer = StringIndexer(inputCol="roadway_surface_cond", outputCol="roadway_surface_cond_index")

# Assemble all features into a single vector
assembler = VectorAssembler(
    inputCols=[
        "weather_condition_index",
        "lighting_condition_index",
        "roadway_surface_cond_index",
        "crash_day_of_week",
        "crash_hour"
    ],
    outputCol="features"
)

# Random Forest Model 
rf = RandomForestClassifier(
    labelCol="crash_month", 
    featuresCol="features",
    numTrees=150,       
    maxDepth=5,          
    seed=42
)

# Create Pipeline
pipeline = Pipeline(stages=[weather_indexer, lighting_indexer, roadway_indexer, assembler, rf])

# Train-test split
train_data, test_data = crash.randomSplit([0.8, 0.2], seed=42)

# Fit model
model = pipeline.fit(train_data)

# Predict
predictions = model.transform(test_data)

# Evaluation Metrics
evaluator_acc = MulticlassClassificationEvaluator(labelCol="crash_month", predictionCol="prediction", metricName="accuracy")
accuracy = evaluator_acc.evaluate(predictions)

evaluator_f1 = MulticlassClassificationEvaluator(labelCol="crash_month", predictionCol="prediction", metricName="f1")
f1_score = evaluator_f1.evaluate(predictions)

print(f"Random Forest Test Accuracy = {accuracy:.4f}")
print(f"Random Forest Test F1 Score = {f1_score:.4f}")

# Confusion Matrix
confusion = predictions.groupBy("crash_month", "prediction").count().toPandas()

pivot = confusion.pivot(index='crash_month', columns='prediction', values='count').fillna(0)

plt.figure(figsize=(12, 8))
sns.heatmap(pivot, annot=True, fmt=".0f", cmap="Blues")
plt.title("Random Forest Confusion Matrix")
plt.xlabel("Predicted Month")
plt.ylabel("Actual Month")
plt.show()

# Optional: Cross-Validation for Random Forest
paramGrid = ParamGridBuilder() \
    .addGrid(rf.numTrees, [100, 150]) \
    .addGrid(rf.maxDepth, [3, 5]) \
    .build()

crossval = CrossValidator(
    estimator=pipeline,
    estimatorParamMaps=paramGrid,
    evaluator=MulticlassClassificationEvaluator(labelCol="crash_month", predictionCol="prediction", metricName="f1"),
    numFolds=5,
    parallelism=2
)

cv_model = crossval.fit(train_data)

print("Best Random Forest Model after Cross Validation:")
best_rf_model = cv_model.bestModel.stages[-1]
print(f"  - Best Num Trees: {best_rf_model.getNumTrees}")
print(f"  - Best Max Depth: {best_rf_model.getOrDefault('maxDepth')}")

# Final Evaluation on test set with Cross-Validated model
cv_predictions = cv_model.transform(test_data)

accuracy_cv = evaluator_acc.evaluate(cv_predictions)
f1_score_cv = evaluator_f1.evaluate(cv_predictions)

print(f"Cross-Validated Test Accuracy = {accuracy_cv:.4f}")
print(f"Cross-Validated Test F1 Score = {f1_score_cv:.4f}")

In [0]:
## Pull cleaned data
crash = crashmaster

from pyspark.sql.functions import col, hour, dayofweek, to_timestamp, lit, rand
from pyspark.sql.types import IntegerType
from pyspark.ml.feature import StringIndexer, VectorAssembler
from pyspark.ml.classification import RandomForestClassifier
from pyspark.ml.evaluation import MulticlassClassificationEvaluator
from pyspark.ml.tuning import ParamGridBuilder, CrossValidator
import matplotlib.pyplot as plt
import seaborn as sns

# ========== Feature Engineering ==========
# Check if 'crash_time' exists
if 'crash_time' in crash.columns:
    crash = crash.withColumn("crash_time", to_timestamp("crash_time"))
    crash = crash.withColumn("day_of_week", (dayofweek("crash_time") - 1).cast(IntegerType()))
    crash = crash.withColumn("hour_of_day", hour("crash_time").cast(IntegerType()))
else:
    # Create random day_of_week and hour_of_day if missing
    crash = crash.withColumn("day_of_week", (lit(rand() * 7).cast(IntegerType())))
    crash = crash.withColumn("hour_of_day", (lit(rand() * 24).cast(IntegerType())))

# ========== Data Preprocessing ==========
# Drop rows with missing critical information
crash = crash.dropna(subset=["crash_month", "weather_condition", "lighting_condition", "roadway_surface_cond"])

# ========== Train/Test Split ==========
train_set, test_set = crash.randomSplit([0.8, 0.2], seed=42)



com.databricks.backend.common.rpc.CommandSkippedException
	at com.databricks.spark.chauffeur.SequenceExecutionState.$anonfun$cancel$3(SequenceExecutionState.scala:138)
	at com.databricks.spark.chauffeur.SequenceExecutionState.$anonfun$cancel$3$adapted(SequenceExecutionState.scala:133)
	at scala.collection.immutable.Range.foreach(Range.scala:158)
	at com.databricks.spark.chauffeur.SequenceExecutionState.cancel(SequenceExecutionState.scala:133)
	at com.databricks.spark.chauffeur.ExecContextState.cancelRunningSequence(ExecContextState.scala:728)
	at com.databricks.spark.chauffeur.ExecContextState.$anonfun$cancel$1(ExecContextState.scala:446)
	at scala.Option.getOrElse(Option.scala:189)
	at com.databricks.spark.chauffeur.ExecContextState.cancel(ExecContextState.scala:446)
	at com.databricks.spark.chauffeur.ExecutionContextManagerV1.cancelExecution(ExecutionContextManagerV1.scala:464)
	at com.databricks.spark.chauffeur.ChauffeurState.$anonfun$process$1(ChauffeurState.scala:571)
	at com.data

In [0]:
# ========== Encoding Categorical Features ==========
indexers = [
    StringIndexer(inputCol="weather_condition", outputCol="weather_encoded"),
    StringIndexer(inputCol="lighting_condition", outputCol="light_encoded"),
    StringIndexer(inputCol="roadway_surface_cond", outputCol="road_encoded")
]

# Build a feature assembler
feature_cols = ["weather_encoded", "light_encoded", "road_encoded", "day_of_week", "hour_of_day"]
assembler = VectorAssembler(inputCols=feature_cols, outputCol="features")

pipeline = Pipeline(stages=indexers + [assembler])
pipeline_model = pipeline.fit(train_set)

train_prepared = pipeline_model.transform(train_set)
test_prepared = pipeline_model.transform(test_set)


com.databricks.backend.common.rpc.CommandSkippedException
	at com.databricks.spark.chauffeur.SequenceExecutionState.$anonfun$cancel$3(SequenceExecutionState.scala:138)
	at com.databricks.spark.chauffeur.SequenceExecutionState.$anonfun$cancel$3$adapted(SequenceExecutionState.scala:133)
	at scala.collection.immutable.Range.foreach(Range.scala:158)
	at com.databricks.spark.chauffeur.SequenceExecutionState.cancel(SequenceExecutionState.scala:133)
	at com.databricks.spark.chauffeur.ExecContextState.cancelRunningSequence(ExecContextState.scala:728)
	at com.databricks.spark.chauffeur.ExecContextState.$anonfun$cancel$1(ExecContextState.scala:446)
	at scala.Option.getOrElse(Option.scala:189)
	at com.databricks.spark.chauffeur.ExecContextState.cancel(ExecContextState.scala:446)
	at com.databricks.spark.chauffeur.ExecutionContextManagerV1.cancelExecution(ExecutionContextManagerV1.scala:464)
	at com.databricks.spark.chauffeur.ChauffeurState.$anonfun$process$1(ChauffeurState.scala:571)
	at com.data

In [0]:
# ========== Modeling: Random Forest ==========
rf = RandomForestClassifier(labelCol="crash_month", featuresCol="features", seed=42)
rf_model = rf.fit(train_prepared)

# Predictions
train_pred = rf_model.transform(train_prepared)
test_pred = rf_model.transform(test_prepared)

# ========== Evaluation ==========
evaluator = MulticlassClassificationEvaluator(
    labelCol="crash_month", predictionCol="prediction", metricName="f1"
)

train_f1 = evaluator.evaluate(train_pred)
test_f1 = evaluator.evaluate(test_pred)

print(f"Train F1 Score (Random Forest): {train_f1}")
print(f"Test F1 Score (Random Forest): {test_f1}")

com.databricks.backend.common.rpc.CommandSkippedException
	at com.databricks.spark.chauffeur.SequenceExecutionState.$anonfun$cancel$3(SequenceExecutionState.scala:138)
	at com.databricks.spark.chauffeur.SequenceExecutionState.$anonfun$cancel$3$adapted(SequenceExecutionState.scala:133)
	at scala.collection.immutable.Range.foreach(Range.scala:158)
	at com.databricks.spark.chauffeur.SequenceExecutionState.cancel(SequenceExecutionState.scala:133)
	at com.databricks.spark.chauffeur.ExecContextState.cancelRunningSequence(ExecContextState.scala:728)
	at com.databricks.spark.chauffeur.ExecContextState.$anonfun$cancel$1(ExecContextState.scala:446)
	at scala.Option.getOrElse(Option.scala:189)
	at com.databricks.spark.chauffeur.ExecContextState.cancel(ExecContextState.scala:446)
	at com.databricks.spark.chauffeur.ExecutionContextManagerV1.cancelExecution(ExecutionContextManagerV1.scala:464)
	at com.databricks.spark.chauffeur.ChauffeurState.$anonfun$process$1(ChauffeurState.scala:571)
	at com.data

In [0]:
# ========== Confusion Matrix ==========
# Extract predictions for plotting
y_true = test_pred.select("crash_month").rdd.flatMap(lambda x: x).collect()
y_pred = test_pred.select("prediction").rdd.flatMap(lambda x: x).collect()

# Plot confusion matrix
plt.figure(figsize=(12,8))
sns.heatmap(confusion_matrix(y_true, y_pred), annot=True, fmt="d", cmap="Blues")
plt.title("Random Forest Confusion Matrix")
plt.xlabel("Predicted Month")
plt.ylabel("Actual Month")
plt.show()

com.databricks.backend.common.rpc.CommandSkippedException
	at com.databricks.spark.chauffeur.SequenceExecutionState.$anonfun$cancel$3(SequenceExecutionState.scala:138)
	at com.databricks.spark.chauffeur.SequenceExecutionState.$anonfun$cancel$3$adapted(SequenceExecutionState.scala:133)
	at scala.collection.immutable.Range.foreach(Range.scala:158)
	at com.databricks.spark.chauffeur.SequenceExecutionState.cancel(SequenceExecutionState.scala:133)
	at com.databricks.spark.chauffeur.ExecContextState.cancelRunningSequence(ExecContextState.scala:728)
	at com.databricks.spark.chauffeur.ExecContextState.$anonfun$cancel$1(ExecContextState.scala:446)
	at scala.Option.getOrElse(Option.scala:189)
	at com.databricks.spark.chauffeur.ExecContextState.cancel(ExecContextState.scala:446)
	at com.databricks.spark.chauffeur.ExecutionContextManagerV1.cancelExecution(ExecutionContextManagerV1.scala:464)
	at com.databricks.spark.chauffeur.ChauffeurState.$anonfun$process$1(ChauffeurState.scala:571)
	at com.data

In [0]:

# ========== Cross-Validation ==========
paramGrid = (ParamGridBuilder()
             .addGrid(rf.numTrees, [50, 100])
             .addGrid(rf.maxDepth, [5, 10])
             .build())

crossval = CrossValidator(estimator=rf,
                          estimatorParamMaps=paramGrid,
                          evaluator=evaluator,
                          numFolds=3)

cv_model = crossval.fit(train_prepared)

# Best model evaluation
best_model = cv_model.bestModel
best_test_pred = best_model.transform(test_prepared)
best_test_f1 = evaluator.evaluate(best_test_pred)

print(f"Best Cross-Validated F1 Score (Random Forest): {best_test_f1}")

com.databricks.backend.common.rpc.CommandSkippedException
	at com.databricks.spark.chauffeur.SequenceExecutionState.$anonfun$cancel$3(SequenceExecutionState.scala:138)
	at com.databricks.spark.chauffeur.SequenceExecutionState.$anonfun$cancel$3$adapted(SequenceExecutionState.scala:133)
	at scala.collection.immutable.Range.foreach(Range.scala:158)
	at com.databricks.spark.chauffeur.SequenceExecutionState.cancel(SequenceExecutionState.scala:133)
	at com.databricks.spark.chauffeur.ExecContextState.cancelRunningSequence(ExecContextState.scala:728)
	at com.databricks.spark.chauffeur.ExecContextState.$anonfun$cancel$1(ExecContextState.scala:446)
	at scala.Option.getOrElse(Option.scala:189)
	at com.databricks.spark.chauffeur.ExecContextState.cancel(ExecContextState.scala:446)
	at com.databricks.spark.chauffeur.ExecutionContextManagerV1.cancelExecution(ExecutionContextManagerV1.scala:464)
	at com.databricks.spark.chauffeur.ChauffeurState.$anonfun$process$1(ChauffeurState.scala:571)
	at com.data

In [0]:
from pyspark.sql import functions as F
from pyspark.ml.feature import StringIndexer, VectorAssembler
from pyspark.ml.classification import DecisionTreeClassifier
from pyspark.ml.regression import LinearRegression
from pyspark.ml import Pipeline
from pyspark.ml.evaluation import MulticlassClassificationEvaluator, RegressionEvaluator

mastercrash = spark.read.csv("dbfs:/FileStore/shared_uploads/finalprojectgroup4040@gmail.com/export__1_.csv", header=True, inferSchema=True)

# Temp file
crash = mastercrash

def analyze_weather_impact(crash, train_ratio=0.7, seed=42):

    # 1. Weather Condition vs. Crash Type Analysis (Classification)
    print("\n--- 1. Weather Condition vs. Crash Type Analysis ---")

    # Prepare data for classification
    df_crash_type = crash.select("weather_condition", "crash_type").dropna()  # Remove nulls for this analysis

    # String Indexer for weather_condition and crash_type
    weather_indexer = StringIndexer(inputCol="weather_condition", outputCol="weather_index", handleInvalid="keep")
    crash_type_indexer = StringIndexer(inputCol="crash_type", outputCol="label", handleInvalid="keep")

    # Vector Assembler for features (weather_index)
    assembler_crash_type = VectorAssembler(inputCols=["weather_index"], outputCol="features")

    # Decision Tree Classifier
    dtc = DecisionTreeClassifier(featuresCol="features", labelCol="label", maxDepth=4)

    # Pipeline
    pipeline_crash_type = Pipeline(stages=[weather_indexer, crash_type_indexer, assembler_crash_type, dtc])

    # Train/test split
    train_crash_type, test_crash_type = df_crash_type.randomSplit([train_ratio, 1 - train_ratio], seed=seed)

    # Fit model
    model_crash_type = pipeline_crash_type.fit(train_crash_type)

    # Predict
    predictions_crash_type = model_crash_type.transform(test_crash_type)

    # Evaluate (Accuracy)
    evaluator_crash_type = MulticlassClassificationEvaluator(labelCol="label", predictionCol="prediction", metricName="accuracy")
    accuracy_crash_type = evaluator_crash_type.evaluate(predictions_crash_type)
    print(f"   Test Accuracy (Crash Type Prediction): {accuracy_crash_type:.4f}")

    # Show a sample of predictions
    predictions_crash_type.select("weather_condition", "crash_type", "prediction", "label").show(10)

    # 2. Weather Condition vs. Fatalities Analysis (Regression)
    print("\n--- 2. Weather Condition vs. Fatalities Analysis ---")

    # Prepare data for regression
    df_fatalities = crash.select("weather_condition", "injuries_fatal").dropna() # Remove nulls

    # String Indexer for weather condition
    weather_indexer_fatal = StringIndexer(inputCol="weather_condition", outputCol="weather_index", handleInvalid="keep")

    # Vector Assembler for features (weather_index)
    assembler_fatalities = VectorAssembler(inputCols=["weather_index"], outputCol="features") 

    # Linear Regression
    lr = LinearRegression(featuresCol="features", labelCol="injuries_fatal")

    # Pipeline
    pipeline_fatalities = Pipeline(stages=[weather_indexer_fatal, assembler_fatalities, lr]) 

    # Train/test split
    train_fatalities, test_fatalities = df_fatalities.randomSplit([train_ratio, 1 - train_ratio], seed=seed)

    # Fit model
    model_fatalities = pipeline_fatalities.fit(train_fatalities)

    # Predict
    predictions_fatalities = model_fatalities.transform(test_fatalities)

    # Evaluate (R-squared)
    evaluator_fatalities = RegressionEvaluator(labelCol="injuries_fatal", predictionCol="prediction", metricName="r2")
    r2_fatalities = evaluator_fatalities.evaluate(predictions_fatalities)
    print(f"   Test R-squared (Fatalities Prediction): {r2_fatalities:.4f}")

    # Show a sample of predictions
    predictions_fatalities.select("weather_condition", "injuries_fatal", "prediction").show(10)

    # Group by weather condition and show average fatalities
    crash.groupBy("weather_condition").agg(F.mean("injuries_fatal").alias("avg_fatalities")).orderBy("avg_fatalities", ascending=False).show()

# Assuming your cleaned DataFrame is named 'crash'
analyze_weather_impact(crash)


--- 1. Weather Condition vs. Crash Type Analysis ---
   Test Accuracy (Crash Type Prediction): 0.5646
+-----------------+--------------------+----------+-----+
|weather_condition|          crash_type|prediction|label|
+-----------------+--------------------+----------+-----+
|     BLOWING SNOW|INJURY AND / OR T...|       0.0|  1.0|
|     BLOWING SNOW|INJURY AND / OR T...|       0.0|  1.0|
|     BLOWING SNOW|INJURY AND / OR T...|       0.0|  1.0|
|     BLOWING SNOW|INJURY AND / OR T...|       0.0|  1.0|
|     BLOWING SNOW|NO INJURY / DRIVE...|       0.0|  0.0|
|     BLOWING SNOW|NO INJURY / DRIVE...|       0.0|  0.0|
|     BLOWING SNOW|NO INJURY / DRIVE...|       0.0|  0.0|
|     BLOWING SNOW|NO INJURY / DRIVE...|       0.0|  0.0|
|     BLOWING SNOW|NO INJURY / DRIVE...|       0.0|  0.0|
|     BLOWING SNOW|NO INJURY / DRIVE...|       0.0|  0.0|
+-----------------+--------------------+----------+-----+
only showing top 10 rows


--- 2. Weather Condition vs. Fatalities Analysis ---
   Te